use gene_GEP mapping df to run linear regression model to use other GEPs to try and predict GEP 15

also try xgboost/randomforestregressor sklearn

In [1]:
import pandas as pd
import scanpy as sc
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.linear_model import ElasticNetCV, LinearRegression
from sklearn.model_selection import train_test_split

pd.set_option('display.max_columns', None)

# gene-GEP mapping model fits

In [2]:
gene_GEP_mapping = pd.read_csv(r'./data/Factorized matrices from human lifetime scRNA(Gene Z-score x GEP).csv').set_index('Gene')
gene_GEP_mapping.head()

GEP 1 (Mono/DC)  GEP 2 (single donor-specific)     GEP 3  \
Gene                                                                   
X5S-rRNA           0.000052                       0.000116  0.000263   
X5-8S-rRNA        -0.000103                       0.000006 -0.000108   
X7SK              -0.000016                       0.000140  0.000461   
A1BG               0.000171                       0.000117 -0.000189   
A1BG.AS1           0.000117                       0.000149  0.000394   

            GEP 4 (Elderly-HSC)     GEP 5     GEP 6     GEP 7     GEP 8  \
Gene                                                                      
X5S-rRNA              -0.000159  0.000005 -0.000078 -0.000068  0.000133   
X5-8S-rRNA            -0.000053 -0.000018 -0.000056 -0.000023 -0.000036   
X7SK                  -0.000180 -0.000021 -0.000083 -0.000011  0.000109   
A1BG                  -0.000157  0.000059  0.000545 -0.000263 -0.000040   
A1BG.AS1               0.000058 -0.000030 -0.000047  0.000091  0.000076   

               GEP 9    GEP 10    GEP 11    GEP 12    GEP 13  GEP 14 (Meg)  \
Gene                                                                         
X5S-rRNA    0.000013  0.000045 -0.000144 -0.000159  0.000101      0.000155   
X5-8S-rRNA  0.000012 -0.000088  0.000249 -0.000041 -0.000026     -0.000056   
X7SK        0.000092  0.000473 -0.000136  0.000092  0.000043      0.000287   
A1BG        0.000030 -0.000020 -0.000174  0.000339 -0.000053      0.000133   
A1BG.AS1   -0.000044  0.000401 -0.000060 -0.000090 -0.000006     -0.000123   

            GEP 15 (DNA Replication)    GEP 16    GEP 17    GEP 18    GEP 19  \
Gene                                                                           
X5S-rRNA                   -0.000043  0.000404  0.000694 -0.000127 -0.000320   
X5-8S-rRNA                 -0.000039  0.000015 -0.000085  0.000005 -0.000121   
X7SK                       -0.000040  0.000058 -0.000144  0.000510 -0.000146   
A1BG                       -0.000166 -0.000044  0.000426 -0.000105 -0.000281   
A1BG.AS1                   -0.000162  0.000425 -0.000090  0.000057  0.000134   

              GEP 20  GEP 21 (Mitochondiral genes)  GEP 22 (Cell cycle)  \
Gene                                                                      
X5S-rRNA    0.000706                     -0.000357        -1.419610e-04   
X5-8S-rRNA -0.000155                     -0.000155        -5.680000e-07   
X7SK        0.000467                     -0.000417        -1.021400e-04   
A1BG        0.000505                     -0.000388        -2.606410e-04   
A1BG.AS1   -0.000032                     -0.000445        -1.729850e-04   

              GEP 23    GEP 24  GEP 25 (Baso/Mast)  GEP 26 (Lymphoid)  \
Gene                                                                    
X5S-rRNA   -0.000007 -0.000191            0.000056           0.000002   
X5-8S-rRNA  0.000009  0.000040            0.000063          -0.000019   
X7SK        0.000051 -0.000145            0.000062           0.000006   
A1BG       -0.000047  0.000385           -0.000028           0.000142   
A1BG.AS1   -0.000015 -0.000243            0.000162           0.000269   

            GEP 27 (Ribosomal biogenesis)  GEP 28 (Fetal-HSC)    GEP 29  \
Gene                                                                      
X5S-rRNA                         0.000134           -0.000127  0.000497   
X5-8S-rRNA                      -0.000010           -0.000085  0.000517   
X7SK                            -0.000086            0.000201  0.000052   
A1BG                             0.000048            0.000055 -0.000144   
A1BG.AS1                        -0.000310            0.000103 -0.000104   

            GEP 30 (Granulocyte)    GEP 31  GEP 32 (Erythroid)  \
Gene                                                             
X5S-rRNA                0.000069  0.000093            0.000020   
X5-8S-rRNA              0.000008 -0.000006           -0.000026   
X7SK                    0.000089  0.000155   

In [3]:
def get_X_gene():
    return gene_GEP_mapping.drop('GEP 15 (DNA Replication)', axis=1)

def get_y_gene():
    return gene_GEP_mapping['GEP 15 (DNA Replication)']

In [4]:
X_gene_train, X_gene_test, y_gene_train, y_gene_test = train_test_split(get_X_gene(), get_y_gene(), test_size=0.2)

alphas = np.logspace(-6, 6, 500)
l1_ratios = [0.0, 0.01, 0.025, 0.05, 0.1, 0.3, 0.5, 0.7, 0.9, 0.95, 0.97, 1.0]

gene_elastic = ElasticNetCV(alphas=alphas, l1_ratio=l1_ratios, cv=10, n_jobs=-1)
gene_elastic.fit(X_gene_train, y_gene_train)

c:\Users\suchi\anaconda3\envs\hsc\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:683: UserWarning: Coordinate descent without L1 regularization may lead to unexpected results and is discouraged. Set l1_ratio > 0 to add L1 regularization.
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\suchi\anaconda3\envs\hsc\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:683: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.0008573886271511749, tolerance: 1.7147772543026002e-07
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\suchi\anaconda3\envs\hsc\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:683: UserWarning: Coordinate descent without L1 regularization may lead to unexpected results and is discouraged. Set l1_ratio > 0 to add L1 regularization.
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\suchi\anaconda3\envs\hsc\lib\site-packages\sklearn\linear_model\_coor

ElasticNetCV(alphas=array([1.00000000e-06, 1.05693455e-06, 1.11711065e-06, 1.18071285e-06,
       1.24793621e-06, 1.31898690e-06, 1.39408283e-06, 1.47345431e-06,
       1.55734477e-06, 1.64601150e-06, 1.73972643e-06, 1.83877698e-06,
       1.94346693e-06, 2.05411735e-06, 2.17106760e-06, 2.29467637e-06,
       2.42532274e-06, 2.56340741e-06, 2.70935387e-06, 2.86360972e-06,
       3.02664806e-06, 3.198968...
       3.49209598e+05, 3.69091691e+05, 3.90105762e+05, 4.12316259e+05,
       4.35791301e+05, 4.60602884e+05, 4.86827104e+05, 5.14544388e+05,
       5.43839743e+05, 5.74803016e+05, 6.07529169e+05, 6.42118571e+05,
       6.78677305e+05, 7.17317494e+05, 7.58157646e+05, 8.01323013e+05,
       8.46945981e+05, 8.95166472e+05, 9.46132376e+05, 1.00000000e+06]),
             cv=10,
             l1_ratio=[0.0, 0.01, 0.025, 0.05, 0.1, 0.3, 0.5, 0.7, 0.9, 0.95,
                       0.97, 1.0],
             n_jobs=-1)

In [12]:
print(f'optimal gene alpha: {gene_elastic.alpha_}')
print(f'optimal gene l1_ratio: {gene_elastic.l1_ratio_}')
print(f'elastic net gene test R^2: {gene_elastic.score(X_gene_test, y_gene_test)}')

optimal gene alpha: 1e-06
optimal gene l1_ratio: 0.0
elastic net gene test R^2: 0.17126908849965827


In [6]:
gene_LR = LinearRegression()

gene_LR.fit(X_gene_train, y_gene_train)

LinearRegression()

In [13]:
print(f'base linear regression gene test R^2: {gene_LR.score(X_gene_test, y_gene_test)}')

base linear regression gene test R^2: 0.9550133278852434


# cell-GEP mapping model fits

In [8]:
cell_GEP_mapping = pd.read_csv(r'./data/Factorized matrices from human lifetime scRNA(GEP usage per cell).csv').set_index('Cell')
cell_GEP_mapping.head()

GEP 1 (Mono/DC)  GEP 2 (single donor-specific)     GEP 3  \
Cell                                                                   
BM1_bcBSQM         0.036803                       0.026881  0.012481   
BM1_bcCHLB         0.010666                       0.000000  0.000000   
BM1_bcFZFC         0.062572                       0.000000  0.006028   
BM1_bcGZEW         0.045451                       0.031609  0.000000   
BM1_bcFMRM         0.041508                       0.000000  0.000000   

            GEP 4 (Elderly-HSC)     GEP 5  GEP 6     GEP 7     GEP 8  \
Cell                                                                   
BM1_bcBSQM             0.464846  0.000000    0.0  0.000000  0.000000   
BM1_bcCHLB             0.435595  0.000000    0.0  0.020563  0.011753   
BM1_bcFZFC             0.396839  0.000000    0.0  0.000000  0.007984   
BM1_bcGZEW             0.517612  0.000000    0.0  0.000000  0.009147   
BM1_bcFMRM             0.302918  0.000057    0.0  0.000000  0.000000   

               GEP 9    GEP 10    GEP 11    GEP 12    GEP 13  GEP 14 (Meg)  \
Cell                                                                         
BM1_bcBSQM  0.000000  0.000000  0.000645  0.002771  0.000000      0.000000   
BM1_bcCHLB  0.016536  0.017280  0.000000  0.033893  0.000681      0.029359   
BM1_bcFZFC  0.047616  0.005497  0.000000  0.000000  0.000000      0.026648   
BM1_bcGZEW  0.031807  0.000000  0.006016  0.000000  0.000000      0.016127   
BM1_bcFMRM  0.000000  0.000000  0.000000  0.003737  0.000000      0.000000   

            GEP 15 (DNA Replication)  GEP 16    GEP 17    GEP 18  GEP 19  \
Cell                                                                       
BM1_bcBSQM                  0.111207     0.0  0.001688  0.000000     0.0   
BM1_bcCHLB                  0.070330     0.0  0.000000  0.000000     0.0   
BM1_bcFZFC                  0.161894     0.0  0.000000  0.001741     0.0   
BM1_bcGZEW                  0.083941     0.0  0.000000  0.000000     0.0   
BM1_bcFMRM                  0.225007     0.0  0.000000  0.010482     0.0   

              GEP 20  GEP 21 (Mitochondiral genes)  GEP 22 (Cell cycle)  \
Cell                                                                      
BM1_bcBSQM  0.000000                      0.038902             0.000383   
BM1_bcCHLB  0.000000                      0.041981             0.000000   
BM1_bcFZFC  0.018964                      0.030627             0.003311   
BM1_bcGZEW  0.000000                      0.036858             0.000000   
BM1_bcFMRM  0.003365                      0.064948             0.004206   

            GEP 23    GEP 24  GEP 25 (Baso/Mast)  GEP 26 (Lymphoid)  \
Cell                                                                  
BM1_bcBSQM  0.0000  0.001779             0.00000           0.065462   
BM1_bcCHLB  0.0065  0.003607             0.00000           0.000000   
BM1_bcFZFC  0.0000  0.000068             0.00000           0.002143   
BM1_bcGZEW  0.0000  0.000000             0.00003           0.004162   
BM1_bcFMRM  0.0000  0.000000             0.00000           0.000000   

            GEP 27 (Ribosomal biogenesis)  GEP 28 (Fetal-HSC)    GEP 29  \
Cell                                                                      
BM1_bcBSQM                       0.179906                 0.0  0.000000   
BM1_bcCHLB                       0.043055                 0.0  0.000000   
BM1_bcFZFC                       0.058599                 0.0  0.000046   
BM1_bcGZEW                       0.113646                 0.0  0.000000   
BM1_bcFMRM                       0.102505                 0.0  0.000000   

            GEP 30 (Granulocyte)    GEP 31  GEP 32 (Erythroid)  \
Cell                                                             
BM1_bcBSQM              0.014643  0.010171            0.000000   
BM1_bcCHLB              0.002227  0.016027            0.018264   
BM1_bcFZFC              0.010492  0.000000            0.000000   
BM1_bcGZEW              0.000000  0.000000

In [9]:
def get_X_cell():
    return cell_GEP_mapping.drop('GEP 15 (DNA Replication)', axis=1)

def get_y_cell():
    return cell_GEP_mapping['GEP 15 (DNA Replication)']

In [10]:
X_cell_train, X_cell_test, y_cell_train, y_cell_test = train_test_split(get_X_cell(), get_y_cell(), test_size=0.2)

alphas = np.logspace(-6, 6, 500)
l1_ratios = [0.0, 0.01, 0.025, 0.05, 0.1, 0.3, 0.5, 0.7, 0.9, 0.95, 0.97, 1.0]

cell_elastic = ElasticNetCV(alphas=alphas, l1_ratio=l1_ratios, cv=10, n_jobs=-1)
cell_elastic.fit(X_cell_train, y_cell_train)

c:\Users\suchi\anaconda3\envs\hsc\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:683: UserWarning: Coordinate descent without L1 regularization may lead to unexpected results and is discouraged. Set l1_ratio > 0 to add L1 regularization.
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\suchi\anaconda3\envs\hsc\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:683: UserWarning: Coordinate descent without L1 regularization may lead to unexpected results and is discouraged. Set l1_ratio > 0 to add L1 regularization.
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\suchi\anaconda3\envs\hsc\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:683: UserWarning: Coordinate descent without L1 regularization may lead to unexpected results and is discouraged. Set l1_ratio > 0 to add L1 regularization.
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\suchi\anaconda3\envs\hsc\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:6

ElasticNetCV(alphas=array([1.00000000e-06, 1.05693455e-06, 1.11711065e-06, 1.18071285e-06,
       1.24793621e-06, 1.31898690e-06, 1.39408283e-06, 1.47345431e-06,
       1.55734477e-06, 1.64601150e-06, 1.73972643e-06, 1.83877698e-06,
       1.94346693e-06, 2.05411735e-06, 2.17106760e-06, 2.29467637e-06,
       2.42532274e-06, 2.56340741e-06, 2.70935387e-06, 2.86360972e-06,
       3.02664806e-06, 3.198968...
       3.49209598e+05, 3.69091691e+05, 3.90105762e+05, 4.12316259e+05,
       4.35791301e+05, 4.60602884e+05, 4.86827104e+05, 5.14544388e+05,
       5.43839743e+05, 5.74803016e+05, 6.07529169e+05, 6.42118571e+05,
       6.78677305e+05, 7.17317494e+05, 7.58157646e+05, 8.01323013e+05,
       8.46945981e+05, 8.95166472e+05, 9.46132376e+05, 1.00000000e+06]),
             cv=10,
             l1_ratio=[0.0, 0.01, 0.025, 0.05, 0.1, 0.3, 0.5, 0.7, 0.9, 0.95,
                       0.97, 1.0],
             n_jobs=-1)

In [11]:
print(f'optimal cell alpha: {cell_elastic.alpha_}')
print(f'optimal cell l1_ratio: {cell_elastic.l1_ratio_}')
print(f'elastic net cell test R^2: {cell_elastic.score(X_cell_test, y_cell_test)}')

optimal cell alpha: 1e-06
optimal cell l1_ratio: 0.0
elastic net cell test R^2: 0.9999942918549471


In [14]:
cell_LR = LinearRegression()

cell_LR.fit(X_cell_train, y_cell_train)

LinearRegression()

In [15]:
print(f'base linear regression cell test R^2: {cell_LR.score(X_cell_test, y_cell_test)}')

base linear regression cell test R^2: 1.0
